# Inputs


### Librerías necesarias

In [11]:
%reset_selective -f b

# Este comando le indica a Python que las figuras se deben generar dentro de la misma Notebook, no en una ventana
## Solo para notebooks.
%matplotlib inline

from matplotlib import pyplot as plt
from matplotlib import colors
import numpy as np
import glob
import pyart
import scipy.io as sio
import re


### Levanto los datos

In [12]:
dia = '20170203'

Levanto los datos de radar 

In [13]:
path_user_radar = './febdBZ/'+ dia + '/'
FileList_radar = np.sort(glob.glob(path_user_radar+'*.nc'))
file2read_radar =FileList_radar[0]
print(file2read_radar)

#Creamos el objeto "radar"
radar = pyart.io.read(file2read_radar)

./febdBZ/20170203/cfrad.20170203_000004.000_to_20170203_000423.001_INTA_Ang_v263_SUR.nc


Levanto los datos de rayos

In [14]:
path_user_rayos = './rayos/201702/'+ dia




with open(path_user_rayos+'.txt') as f:
    lines = f.readlines()

### Armo las celdas

Las grillas las genero en el radar, luego correlaciono la información de rayos.


In [15]:
nelev=0

start_index = radar.sweep_start_ray_index['data'][nelev]
end_index   = radar.sweep_end_ray_index['data'][nelev]

rango  = radar.range['data']
tiempo = radar.time['data'][start_index:end_index]

# Sitio radar
lat_radar = radar.latitude['data'][0]
lon_radar = radar.longitude['data'][0]

# Datos de lat/lon
lats = radar.gate_latitude['data'][start_index:end_index]
lons = radar.gate_longitude['data'][start_index:end_index]

# Datos x/y (en metros)
xdist = radar.gate_x['data'][start_index:end_index]/1000.
ydist = radar.gate_y['data'][start_index:end_index]/1000.

# Variables radar
Zh  = radar.fields['dBZ']['data'][start_index:end_index, :]

In [16]:
iTime = file2read_radar.split('_')[1]
fTime = file2read_radar.split('_')[4]

In [17]:
fTime

'000423.001'

#### Genero la grilla

In [18]:
# mask out last 10 gates of each ray, this removes the "ring" around th radar.
radar.fields['dBZ']['data'][:, -10:] = np.ma.masked

# exclude masked gates from the gridding
gatefilter = pyart.filters.GateFilter(radar)
gatefilter.exclude_transition()
gatefilter.exclude_masked('dBZ')

In [19]:
# perform Cartesian mapping, limit to the reflectivity field.
grid = pyart.map.grid_from_radars(
    (radar,), gatefilters=(gatefilter, ),
    grid_shape=(1, 480, 480),
    grid_limits=((0, 0), (-240000.0, 240000.0), (-240000.0, 240000.0)),
    fields=['dBZ'])

#### Levanto los datos de rayos

In [20]:
tot = len(lines)

latitude = []
longitude = []
time = []
intensity = []

for i in range(tot):
    foo=lines[i].split()
    t=(foo[3]+foo[4]+foo[5])
    #print(foo[7], fTime)
    
    if (t<fTime) and (t>iTime) : 
        
        latitude.append(foo[8])
        longitude.append(foo[7])
        time.append(t)
        intensity.append(foo[9])
    
Rayos = {'Lat': latitude, 'Long': longitude, 'Time': time, 'Int': intensity}

In [21]:
fTime

'000423.001'

In [22]:
lat_grid=grid.get_point_longitude_latitude(level=0, edges=False)[1]
lon_grid=grid.get_point_longitude_latitude(level=0, edges=False)[0]                                                

In [ ]:
ray = np.zeros(lat_grid.shape)

for i in range(479):
    for j in range(479):
          for l in range(len(Rayos['Time'])):
                print(l)
                if (Rayos['Lat'][l] > str(lat_grid[i,j])) and (Rayos['Lat'][l] < str(lat_grid[i,j+1])):
                    if (Rayos['Long'][l]>str(lon_grid[i,j])) and (Rayos['Long'][l]<str(lon_grid[i+1,j])):
                        ray[i,j]=True
                        print(1)
                    else:
                        ray[i,j]=False
                        print(0)
        

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

In [ ]:
ray[0,0]